In [1]:
import os
import numpy as np
import librosa
from pathlib import Path

def extract_melspectrogram(y: np.ndarray, sr: int, n_mels: int = 128, fmax: int = 8000) -> np.ndarray:
    """
    Converts raw audio to a flattened Mel-spectrogram in decibels.

    Args:
        y (np.ndarray): Audio time series.
        sr (int): Sampling rate of `y`.
        n_mels (int): Number of Mel bands.
        fmax (int): Maximum frequency.

    Returns:
        np.ndarray: Flattened Mel-spectrogram (in dB).
    """
    mel = librosa.feature.melspectrogram(y=y, sr=sr, n_mels=n_mels, fmax=fmax)
    mel_db = librosa.power_to_db(mel, ref=np.max)
    mel_db_flat = mel_db.flatten()
    mel_db_fixed = pad_or_truncate(mel_db_flat)
    return mel_db_fixed

def pad_or_truncate(vector: np.ndarray, target_len: int = 128 * 32) -> np.ndarray:
    """Ensure all vectors are exactly `target_len` long (default 4096)."""
    current_len = len(vector)
    if current_len > target_len:
        return vector[:target_len]
    elif current_len < target_len:
        return np.pad(vector, (0, target_len - current_len))
    return vector


def process_audio_file(filepath: str, sr: int = 22050) -> np.ndarray:
    """
    Loads an audio file and computes its Mel-spectrogram features.

    Args:
        filepath (str): Path to the .wav file.
        sr (int): Sampling rate for loading.

    Returns:
        np.ndarray: Flattened Mel-spectrogram.
    """
    y, _ = librosa.load(filepath, sr=sr)
    return extract_melspectrogram(y, sr)

def convert_class_wavs_to_npy(input_dir: str, output_dir: str, label: str, sr: int = 22050) -> None:
    """
    Processes all WAV files of a class (e.g., 'good' or 'bad') and saves them as .npy files.

    Args:
        input_dir (str): Path to the input directory containing class subfolder.
        output_dir (str): Where the .npy files will be saved.
        label (str): Subfolder name (e.g., 'good' or 'bad').
        sr (int): Target sampling rate.
    """
    input_class_dir = os.path.join(input_dir, label)
    output_class_dir = os.path.join(output_dir, label)
    os.makedirs(output_class_dir, exist_ok=True)

    for fname in os.listdir(input_class_dir):
        if fname.endswith(".wav"):
            wav_path = os.path.join(input_class_dir, fname)
            npy_path = os.path.join(output_class_dir, fname.replace(".wav", ".npy"))
            try:
                mel_features = process_audio_file(wav_path, sr)
                print(f"📏 {label.upper()} - {fname}: feature length = {mel_features.shape[0]}")
                np.save(npy_path, mel_features)
                print(f"✅ Saved: {npy_path}")
            except Exception as e:
                print(f"❌ Failed to process {wav_path}: {e}")

def preprocess_client_audio(input_dir: str, output_dir: str, sr: int = 22050) -> None:
    """
    Converts both 'good' and 'bad' labeled audio files for a single client.

    Args:
        input_dir (str): Path to the client's input WAV directory.
        output_dir (str): Output directory for .npy features.
        sr (int): Sampling rate to resample audio.
    """
    print(f"\n🎧 Preprocessing client data from: {input_dir}")
    os.makedirs(output_dir, exist_ok=True)

    for label in ['good', 'bad']:
        convert_class_wavs_to_npy(input_dir, output_dir, label, sr)

def preprocess_all_clients(input_root: str, output_root: str, sr: int = 22050) -> None:
    """
    Processes all clients under a base directory, converting WAVs to Mel-spectrogram .npy files.

    Args:
        input_root (str): Base directory containing client subfolders.
        output_root (str): Destination for processed .npy files.
        sr (int): Sampling rate for all audio files.
    """
    for client in sorted(os.listdir(input_root)):
        input_client_path = os.path.join(input_root, client)
        output_client_path = os.path.join(output_root, client)
        
        if os.path.isdir(input_client_path):
            print(f"\n🚀 Processing client: {client}")
            preprocess_client_audio(input_client_path, output_client_path, sr)


## Preprocess all IID clients

In [2]:
input_base = "../../resources/material/train-data/federated/IID"
output_base = "../../resources/material/train-data/federated/IID-npy"
preprocess_all_clients(input_base, output_base)


🚀 Processing client: client_1

🎧 Preprocessing client data from: ../../resources/material/train-data/federated/IID/client_1
📏 GOOD - good_tap_959_aug_3748.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_959_aug_3748.npy
📏 GOOD - good_tap_952_aug_5417.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_952_aug_5417.npy
📏 GOOD - good_tap_508_aug_349.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_508_aug_349.npy
📏 GOOD - good_tap_138_aug_7720.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_138_aug_7720.npy
📏 GOOD - good_tap_875_aug_2029.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_875_aug_2029.npy
📏 GOOD - good_tap_573_aug_7324.wav: feature length = 4096
✅ Saved: ../..

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/librosa/core/spectrum.py:266: UserWarning: n_fft=2048 is too large for input signal of length=1838
  warnings.warn(


📏 GOOD - good_tap_788_aug_6242.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_788_aug_6242.npy
📏 GOOD - good_tap_400_aug_5881.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_400_aug_5881.npy
📏 GOOD - good_tap_1116_aug_8707.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_1116_aug_8707.npy
📏 GOOD - good_tap_107_aug_8278.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_107_aug_8278.npy
📏 GOOD - good_tap_755_aug_3060.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_755_aug_3060.npy
📏 GOOD - good_tap_1196_org.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/IID-npy/client_1/good/good_tap_1196_org.npy
📏 GOOD - good_tap_1093_aug_384.wav: feat

## Preprocess all non IID clients

In [3]:
input_base = "../../resources/material/train-data/federated/non-IID"
output_base = "../../resources/material/train-data/federated/non-IID-npy"
preprocess_all_clients(input_base, output_base)


🚀 Processing client: client_1

🎧 Preprocessing client data from: ../../resources/material/train-data/federated/non-IID/client_1
📏 GOOD - good_tap_138_aug_7720.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/non-IID-npy/client_1/good/good_tap_138_aug_7720.npy
📏 GOOD - good_tap_185_org.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/non-IID-npy/client_1/good/good_tap_185_org.npy
📏 GOOD - good_tap_1188_aug_7565.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/non-IID-npy/client_1/good/good_tap_1188_aug_7565.npy
📏 GOOD - good_tap_1090_aug_1002.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/non-IID-npy/client_1/good/good_tap_1090_aug_1002.npy
📏 GOOD - good_tap_195_org.wav: feature length = 4096
✅ Saved: ../../resources/material/train-data/federated/non-IID-npy/client_1/good/good_tap_195_org.npy
📏 GOOD - good_tap_1220_aug_5069.wav: feature length = 4096
✅ S

In [4]:
import os
import numpy as np
from pathlib import Path
from collections import defaultdict

def check_npy_lengths(base_dir: str, expected_len: int = 4096):
    """
    Recursively check all `.npy` files under `base_dir` for consistent shape.

    Args:
        base_dir (str): Root directory of the .npy dataset.
        expected_len (int): Expected flattened feature length.
    """
    print(f"\n🔍 Scanning .npy files in: {base_dir}")
    issues = defaultdict(list)
    total_files = 0

    for root, _, files in os.walk(base_dir):
        for fname in files:
            if fname.endswith(".npy"):
                total_files += 1
                npy_path = os.path.join(root, fname)
                try:
                    data = np.load(npy_path)
                    if data.shape[0] != expected_len:
                        issues[data.shape[0]].append(npy_path)
                except Exception as e:
                    print(f"❌ Failed to load {npy_path}: {e}")

    if issues:
        print(f"\n⚠️ Found {sum(len(v) for v in issues.values())} problematic files out of {total_files} scanned.")
        for shape, paths in issues.items():
            print(f"  - Shape {shape}: {len(paths)} files")
            for path in paths[:5]:  # Show first 5
                print(f"    - {path}")
    else:
        print(f"✅ All {total_files} files have correct shape: ({expected_len},)")

# Example usage:
check_npy_lengths("../../resources/material/train-data/federated/IID-npy", expected_len=4096)
check_npy_lengths("../../resources/material/train-data/federated/non-IID-npy", expected_len=4096)



🔍 Scanning .npy files in: ../../resources/material/train-data/federated/IID-npy
✅ All 22050 files have correct shape: (4096,)

🔍 Scanning .npy files in: ../../resources/material/train-data/federated/non-IID-npy
✅ All 22050 files have correct shape: (4096,)
